In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [2]:
emo_text=pd.read_csv("/kaggle/input/emotion-detection/emotion_sentimen_dataset.csv")
emo_text

Unnamed: 0                                               text  Emotion
0                0  i seriously hate one subject to death but now ...     hate
1                1                 im so full of life i feel appalled  neutral
2                2  i sit here to write i start to dig out my feel...  neutral
3                3  ive been really angry with r and i feel like a...    anger
4                4  i feel suspicious if there is no one outside l...  neutral
...            ...                                                ...      ...
839550      839550  i feel like telling these horny devils to find...  neutral
839551      839551  i began to realize that when i was feeling agi...  neutral
839552      839552  i feel very curious be why previous early dawn...  neutral
839553      839553  i feel that becuase of the tyranical nature of...  neutral
839554      839554  i think that after i had spent some time inves...  neutral

[839555 rows x 3 columns]

In [3]:
emo_text["Emotion"].value_counts()

Emotion
neutral       674538
love           39553
happiness      27175
sadness        17481
relief         16729
hate           15267
anger          12336
fun            10075
enthusiasm      9304
surprise        6954
empty           5542
worry           4475
boredom          126
Name: count, dtype: int64

In [4]:
emo_text.count()

Unnamed: 0    839555
text          839555
Emotion       839555
dtype: int64

In [5]:
import transformers
transformers.__version__

'4.35.0'

In [6]:
# !pip install transformers==4.35.0 

In [7]:
# !pip install keras==2.15.0

In [8]:
import tensorflow as tf

device_name = tf.test.gpu_device_name()

if "GPU" not in device_name:
    print("GPU device not found")
    
print('Found GPU at: {}'.format(device_name))

print("GPU", "available (YESS!!!!)" if tf.config.list_physical_devices("GPU") else "not available :(")


2024-06-26 02:26:01.104606: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-06-26 02:26:01.104660: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-06-26 02:26:01.106076: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


Found GPU at: /device:GPU:0
GPU available (YESS!!!!)


In [9]:
strategy = tf.distribute.MirroredStrategy()
print('DEVICES AVAILABLE: {}'.format(strategy.num_replicas_in_sync))

DEVICES AVAILABLE: 2


In [10]:
transformers.__version__

'4.35.0'

In [11]:
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.losses import CategoricalCrossentropy
import tensorflow as tf
from transformers import RobertaTokenizer, TFRobertaModel, RobertaConfig
from tensorflow.keras.layers import Input, Dropout, Dense
from sklearn.model_selection import train_test_split
from tensorflow.keras.initializers import TruncatedNormal
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import EarlyStopping


In [12]:
import tensorflow
tensorflow.__version__

'2.15.0'

In [13]:
import keras
print(keras.__version__)


2.15.0


In [14]:
### --------- Setup Roberta ---------- ###

model_name = 'roberta-base'

# Max length of tokens
max_length = 40
with strategy.scope():
# Load transformers config and set output_hidden_states to False
    config = RobertaConfig.from_pretrained(model_name)
    config.output_hidden_states = False

# Load Roberta tokenizer
    tokenizer = RobertaTokenizer.from_pretrained(pretrained_model_name_or_path = model_name, config = config)

# Load the Roberta model
    transformer_roberta_model = TFRobertaModel.from_pretrained(model_name, config = config)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFRobertaModel: ['lm_head.layer_norm.weight', 'roberta.embeddings.position_ids', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.bias']
- This IS expected if you are initializing TFRobertaModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
Some weights or buffers of the TF 2.0 model TFRobertaModel were not initialized from the PyTorch model and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and infe

In [15]:
data = emo_text[['text', 'Emotion']]

# Set your model output as categorical and save in new label col
data['Emotion_label'] = pd.Categorical(data['Emotion'])

# Transform your output to numeric
data['Emotion'] = data['Emotion_label'].cat.codes

In [16]:
data_train, data_val = train_test_split(data, test_size = 0.2)


In [17]:
data_train.Emotion.value_counts()

Emotion
8     539793
7      31698
5      21824
10     13865
9      13355
6      12166
0       9855
4       8084
3       7390
11      5556
2       4384
12      3563
1        111
Name: count, dtype: int64

In [68]:
data_train.Emotion_label.value_counts()

Emotion_label
neutral       539793
love           31698
happiness      21824
sadness        13865
relief         13355
hate           12166
anger           9855
fun             8084
enthusiasm      7390
surprise        5556
empty           4384
worry           3563
boredom          111
Name: count, dtype: int64

In [18]:
### ------- Build the model ------- ###

with strategy.scope():

# Load the MainLayer
    roberta = transformer_roberta_model.layers[0]

# Build your model input
    input_ids = Input(shape=(max_length,), name='input_ids', dtype='int32')
    inputs = {'input_ids': input_ids}

# Load the Transformers RoBERTa model as a layer in a Keras model
    roberta_model = roberta(inputs)[1]
    dropout = Dropout(config.hidden_dropout_prob, name='pooled_output')
    pooled_output = dropout(roberta_model, training=False)

# Then build your model output
    Emotions = Dense(units=len(data_train.Emotion_label.value_counts()), kernel_initializer=TruncatedNormal(stddev=config.initializer_range), name='sarcastic')(pooled_output)
    outputs = {'Emotion': Emotions}

# And combine it all in a model object
    Robsent = Model(inputs=inputs, outputs=outputs, name='RoBERTa_MultiClass')

# Take a look at the model
    Robsent.summary()

Model: "RoBERTa_MultiClass"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_ids (InputLayer)      [(None, 40)]              0         
                                                                 
 roberta (TFRobertaMainLaye  TFBaseModelOutputWithPo   124645632 
 r)                          olingAndCrossAttentions             
                             (last_hidden_state=(Non             
                             e, 40, 768),                        
                              pooler_output=(None, 7             
                             68),                                
                              past_key_values=None,              
                             hidden_states=None, att             
                             entions=None, cross_att             
                             entions=None)                       
                                                

In [19]:
### ------- Train the model ------- ###

# Set an optimizer
# optimizer = tf.keras.optimizers.legacy.Adam(learning_rate=5e-05,epsilon=1e-08,decay=0.01,clipnorm=1.0)

# # Set loss and metrics
# loss = {'Emotion': CategoricalCrossentropy(from_logits = True)}

# # Compile the model
# Robsent.compile(optimizer = optimizer, loss = loss, metrics = ['accuracy'])

with strategy.scope():

    Robsent.compile(loss=tf.keras.losses.CategoricalCrossentropy(from_logits=True),
                optimizer=tf.keras.optimizers.legacy.Adam(learning_rate=5e-05,epsilon=1e-08,decay=0.01,clipnorm=1.0),
                metrics=['accuracy'])

# Ready output data for the model
    y_train = to_categorical(data_train['Emotion'])

# Tokenize the input (takes some time)
    x_train = tokenizer(
              text=data_train['text'].to_list(),
              add_special_tokens=True,
              max_length=max_length,
              truncation=True,
              padding=True,
              return_tensors='tf',
              return_token_type_ids = False,
              return_attention_mask = True,
              verbose = True)

    y_val = to_categorical(data_val['Emotion'])

    x_val = tokenizer(
              text=data_val['text'].to_list(),
              add_special_tokens=True,
              max_length=max_length,
              truncation=True,
              padding=True,
              return_tensors='tf',
              return_token_type_ids = False,
              return_attention_mask = True,
              verbose = True)

# Fit the model
    history = Robsent.fit(
        x={'input_ids': x_train['input_ids']},
        y={'Emotion': y_train},
        validation_data=({'input_ids': x_val['input_ids']},{'Emotion': y_val}),
        batch_size=64,
        epochs=3,
        verbose=1)

Epoch 1/3
10495/10495 [==============================] - 4116s 387ms/step - loss: 0.0955 - accuracy: 0.9841 - val_loss: 0.0544 - val_accuracy: 0.9913
Epoch 2/3
10495/10495 [==============================] - 4057s 387ms/step - loss: 0.0522 - accuracy: 0.9917 - val_loss: 0.0488 - val_accuracy: 0.9923
Epoch 3/3
10495/10495 [==============================] - 4060s 387ms/step - loss: 0.0485 - accuracy: 0.9923 - val_loss: 0.0475 - val_accuracy: 0.9925


In [20]:
import dill 
dill.load_session('/kaggle/working/state.db')

In [21]:
y_val_predicted = Robsent.predict(
    x={'input_ids': x_val['input_ids']},
)

5248/5248 [==============================] - 292s 54ms/step


In [86]:
y_val_predicted

{'Emotion': array([[ 0.01354233, -1.6935    , -0.73538685, ...,  0.46035656,
         -1.1337055 , -1.6413031 ],
        [-0.2071546 , -1.8911386 , -0.6358716 , ...,  0.35042033,
         -1.5295755 , -1.6921035 ],
        [-0.78836334, -1.8340764 , -0.6910968 , ...,  0.4172432 ,
         -1.5782493 , -1.4944453 ],
        ...,
        [ 0.0589982 , -1.7507253 , -0.5545515 , ...,  0.3482563 ,
         -1.3690621 , -1.8461158 ],
        [-0.16495253, -1.6887879 , -0.7120514 , ...,  0.47480348,
         -1.1157396 , -1.488243  ],
        [-0.32941568, -2.006766  , -1.1419276 , ...,  0.3512334 ,
         -1.5336565 , -1.7548103 ]], dtype=float32)}

In [66]:
import numpy as np
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

# Assuming y_val is one-hot encoded, convert it to true class labels
y_val_true = np.argmax(y_val, axis=1)

# Extract logits for 'Emotion'
logits = y_val_predicted['Emotion']

# Apply softmax to convert logits to probabilities
probabilities = tf.nn.softmax(logits, axis=-1).numpy()

# Get the index of the highest probability for each prediction
y_val_predicted_labels = np.argmax(probabilities, axis=-1)

# Compare the true labels and predicted labels
accuracy = accuracy_score(y_val_true, y_val_predicted_labels)
report = classification_report(y_val_true, y_val_predicted_labels, target_names=emotion_labels)
conf_matrix = confusion_matrix(y_val_true, y_val_predicted_labels)

print("Accuracy:", accuracy)
print("Classification Report:\n", report)
print("Confusion Matrix:\n", conf_matrix)


/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy: 0.9924602914639303
Classification Report:
               precision    recall  f1-score   support

     neutral       0.99      0.96      0.97      2481
        love       0.00      0.00      0.00        15
   happiness       0.99      0.96      0.98      1158
     sadness       1.00      0.98      0.99      1914
      relief       0.99      0.94      0.96      1991
        hate       0.99      0.98      0.98      5351
       anger       0.99      0.97      0.98      3101
         fun       1.00      0.97      0.98      7855
  enthusiasm       0.99      1.00      1.00    134745
    surprise       0.98      0.95      0.97      3374
       empty       1.00      0.95      0.97      3616
       worry       1.00      0.98      0.99      1398
     boredom       0.99      0.96      0.98       912

    accuracy                           0.99    167911
   macro avg       0.92      0.89      0.90    167911
weighted avg       0.99      0.99      0.99    167911

Confusion Matrix:
 [[  238

/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [87]:
probabilities

array([[1.7816637e-04, 3.2319640e-05, 8.4250016e-05, ..., 2.7853181e-04,
        5.6569526e-05, 3.4051445e-05],
       [2.0274369e-04, 3.7635880e-05, 1.3205587e-04, ..., 3.5407802e-04,
        5.4029031e-05, 4.5924258e-05],
       [1.6378771e-04, 5.7561771e-05, 1.8051922e-04, ..., 5.4685166e-04,
        7.4342708e-05, 8.0841361e-05],
       ...,
       [3.6364605e-04, 5.9528622e-05, 1.9688737e-04, ..., 4.8562617e-04,
        8.7192697e-05, 5.4112592e-05],
       [1.4616858e-04, 3.1846437e-05, 8.4576932e-05, ..., 2.7713834e-04,
        5.6484892e-05, 3.8918504e-05],
       [2.6425387e-04, 4.9380680e-05, 1.1726048e-04, ..., 5.2194332e-04,
        7.9254911e-05, 6.3530184e-05]], dtype=float32)

In [88]:
y_val_predicted_labels

array([8, 8, 8, ..., 8, 8, 8])

In [65]:
y_val

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [63]:
y_val_predicted

{'Emotion': array([[ 0.01354233, -1.6935    , -0.73538685, ...,  0.46035656,
         -1.1337055 , -1.6413031 ],
        [-0.2071546 , -1.8911386 , -0.6358716 , ...,  0.35042033,
         -1.5295755 , -1.6921035 ],
        [-0.78836334, -1.8340764 , -0.6910968 , ...,  0.4172432 ,
         -1.5782493 , -1.4944453 ],
        ...,
        [ 0.0589982 , -1.7507253 , -0.5545515 , ...,  0.3482563 ,
         -1.3690621 , -1.8461158 ],
        [-0.16495253, -1.6887879 , -0.7120514 , ...,  0.47480348,
         -1.1157396 , -1.488243  ],
        [-0.32941568, -2.006766  , -1.1419276 , ...,  0.3512334 ,
         -1.5336565 , -1.7548103 ]], dtype=float32)}

In [89]:
import numpy as np
import tensorflow as tf

# Extract logits for 'Emotion'
logits = y_val_predicted['Emotion']

# Apply softmax to convert logits to probabilities
probabilities = tf.nn.softmax(logits, axis=-1).numpy()

# Get the index of the highest probability for each prediction
predicted_indices = np.argmax(probabilities, axis=-1)

# Define the emotion labels in order
emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

# Map the indices to the actual emotion labels
predicted_emotions = [emotion_labels[index] for index in predicted_indices]

# Print the actual predicted emotions
print(predicted_emotions)


['neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'happiness', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'love', 'love', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'happiness', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'love', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'fun', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'fun', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'love', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'worry', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', '

In [61]:
probabilities

array([[1.7816637e-04, 3.2319640e-05, 8.4250016e-05, ..., 2.7853181e-04,
        5.6569526e-05, 3.4051445e-05],
       [2.0274369e-04, 3.7635880e-05, 1.3205587e-04, ..., 3.5407802e-04,
        5.4029031e-05, 4.5924258e-05],
       [1.6378771e-04, 5.7561771e-05, 1.8051922e-04, ..., 5.4685166e-04,
        7.4342708e-05, 8.0841361e-05],
       ...,
       [3.6364605e-04, 5.9528622e-05, 1.9688737e-04, ..., 4.8562617e-04,
        8.7192697e-05, 5.4112592e-05],
       [1.4616858e-04, 3.1846437e-05, 8.4576932e-05, ..., 2.7713834e-04,
        5.6484892e-05, 3.8918504e-05],
       [2.6425387e-04, 4.9380680e-05, 1.1726048e-04, ..., 5.2194332e-04,
        7.9254911e-05, 6.3530184e-05]], dtype=float32)

In [106]:
import numpy as np
import tensorflow as tf
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import pandas as pd

# Extract logits for 'Emotion'
logits = y_val_predicted['Emotion']

# Apply softmax to convert logits to probabilities
probabilities = tf.nn.softmax(logits, axis=-1).numpy()

# Get the index of the highest probability for each prediction
predicted_indices = np.argmax(probabilities, axis=-1)

# Define the emotion labels in order based on the provided mapping
emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

# Map the indices to the actual emotion labels
predicted_emotions = [emotion_labels[index] for index in predicted_indices]

# Assuming y_val is one-hot encoded, convert it to true class labels
y_val_true = np.argmax(y_val, axis=1)

# Map true indices to the actual emotion labels
true_emotions = [emotion_labels[index] for index in y_val_true]

# Print the actual predicted emotions
print("Predicted Emotions:", predicted_emotions)

# Print the true emotions for comparison
print("True Emotions:", true_emotions)

# Optionally, create a DataFrame to view them side by side
comparison_df = pd.DataFrame({
    'True Emotion': true_emotions,
    'Predicted Emotion': predicted_emotions
})

comparison_df

# Compare the true labels and predicted labels
accuracy = accuracy_score(y_val_true, predicted_indices)
report = classification_report(y_val_true, predicted_indices, target_names=emotion_labels)
conf_matrix = confusion_matrix(y_val_true, predicted_indices)

print("Accuracy:", accuracy)
print("Classification Report:\n", report)
print("Confusion Matrix:\n", conf_matrix)


Predicted Emotions: ['neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'happiness', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'love', 'love', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'happiness', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'love', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'fun', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'hate', 'neutral', 'neutral', 'fun', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'love', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'worry', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 

/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy: 0.9924602914639303
Classification Report:
               precision    recall  f1-score   support

       anger       0.99      0.96      0.97      2481
     boredom       0.00      0.00      0.00        15
       empty       0.99      0.96      0.98      1158
  enthusiasm       1.00      0.98      0.99      1914
         fun       0.99      0.94      0.96      1991
   happiness       0.99      0.98      0.98      5351
        hate       0.99      0.97      0.98      3101
        love       1.00      0.97      0.98      7855
     neutral       0.99      1.00      1.00    134745
      relief       0.98      0.95      0.97      3374
     sadness       1.00      0.95      0.97      3616
    surprise       1.00      0.98      0.99      1398
       worry       0.99      0.96      0.98       912

    accuracy                           0.99    167911
   macro avg       0.92      0.89      0.90    167911
weighted avg       0.99      0.99      0.99    167911

Confusion Matrix:
 [[  238

/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/opt/conda/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [91]:
data_val.count()

text             167911
Emotion          167911
Emotion_label    167911
dtype: int64

In [92]:
comparison_df

True Emotion Predicted Emotion
0           neutral           neutral
1           neutral           neutral
2           neutral           neutral
3           neutral           neutral
4           neutral           neutral
...             ...               ...
167906      neutral           neutral
167907       relief            relief
167908      neutral           neutral
167909      neutral           neutral
167910      neutral           neutral

[167911 rows x 2 columns]

In [22]:
import tensorflow as tf
from tensorflow import keras

# Assuming you have a trained model called 'model'
Robsent.save('/kaggle/working/fake_news_emotion_detection.h5')  # Save the model in HDF5 format

/opt/conda/lib/python3.10/site-packages/keras/src/engine/training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [23]:
# To load the model later
loaded_model = keras.models.load_model('/kaggle/working/fake_news_emotion_detection.h5')

In [24]:
# savedModelPath='/kaggle/working/emotionDetection'
# Robsent.module.save_pretrained(savedModelPath)

In [25]:
y_val_predicted

{'Emotion': array([[ 0.01354233, -1.6935    , -0.73538685, ...,  0.46035656,
         -1.1337055 , -1.6413031 ],
        [-0.2071546 , -1.8911386 , -0.6358716 , ...,  0.35042033,
         -1.5295755 , -1.6921035 ],
        [-0.78836334, -1.8340764 , -0.6910968 , ...,  0.4172432 ,
         -1.5782493 , -1.4944453 ],
        ...,
        [ 0.0589982 , -1.7507253 , -0.5545515 , ...,  0.3482563 ,
         -1.3690621 , -1.8461158 ],
        [-0.16495253, -1.6887879 , -0.7120514 , ...,  0.47480348,
         -1.1157396 , -1.488243  ],
        [-0.32941568, -2.006766  , -1.1419276 , ...,  0.3512334 ,
         -1.5336565 , -1.7548103 ]], dtype=float32)}

In [26]:
y_val_predicted_loaded = loaded_model.predict(
    x={'input_ids': x_val['input_ids']},
)

5248/5248 [==============================] - 461s 87ms/step


In [27]:
y_val_predicted_loaded

{'Emotion': array([[ 0.01354139, -1.6934996 , -0.73538566, ...,  0.4603573 ,
         -1.1337047 , -1.6413016 ],
        [-0.20715371, -1.8911393 , -0.6358722 , ...,  0.3504204 ,
         -1.5295756 , -1.6921043 ],
        [-0.78836113, -1.8340755 , -0.69109666, ...,  0.4172427 ,
         -1.5782475 , -1.4944462 ],
        ...,
        [ 0.05899922, -1.7507248 , -0.5545504 , ...,  0.3482559 ,
         -1.3690622 , -1.846116  ],
        [-0.16495214, -1.6887889 , -0.71205235, ...,  0.4748033 ,
         -1.1157408 , -1.4882443 ],
        [-0.32941458, -2.006766  , -1.1419288 , ...,  0.3512323 ,
         -1.5336564 , -1.7548102 ]], dtype=float32)}

In [28]:
# !pip install -q kaggle

In [29]:
# import joblib
# joblib.dump(Robsent, 'robsent.pkl')

In [30]:
import os 
os.chdir(r'/kaggle/working')

In [31]:
from IPython.display import FileLink
FileLink(r'fake_news_emotion_detection.h5')

/kaggle/working/fake_news_emotion_detection.h5

In [32]:
# Robsent.save('path/to/location.keras')

In [33]:
# import tensorflow as tf
# from tensorflow import keras

# # Assuming you have a trained model called 'model'
# Robsent.save('/kaggle/working/fake_news_emotion_detection.h5')  # Save the model in HDF5 format

In [34]:
# from IPython.display import FileLink
# FileLink(r'fake_news_emotion_detection.h5')

In [35]:
# Robsent.summary()

In [36]:
x_val['input_ids']

<tf.Tensor: shape=(167911, 40), dtype=int32, numpy=
array([[   0,  118,  619, ...,    1,    1,    1],
       [   0, 1873,  460, ...,    1,    1,    1],
       [   0,  118,  802, ...,    1,    1,    1],
       ...,
       [   0,  118,   21, ...,    1,    1,    1],
       [   0,  118,  619, ...,    1,    1,    1],
       [   0,  118,  115, ...,    1,    1,    1]], dtype=int32)>

In [43]:
fake_news=pd.read_csv("/kaggle/input/fake-news/train.csv",sep=';')
fake_news

text  label
0      dark agenda behind globalism open border altma...      0
1      america poor still get shaft sami jamil jadall...      0
2      number accuser grow former miss finland accuse...      0
3      heroic prego advertisement replaces refresh we...      0
4      russia syria debbie reynolds thursday even bri...      1
...                                                  ...    ...
16641  comment cost selfdriving taxi really sixtyseve...      0
16642  interest duterte get billion china get money j...      0
16643  forget encyclopaedia get pokiespedia home win ...      0
16644  u election race huma abedin connection minute ...      0
16645  shameful obama legacy white man beat viciously...      0

[16646 rows x 2 columns]

In [46]:
fake_news1=pd.read_csv("/kaggle/input/fake-newss/train.1.csv",sep=';')
fake_news1

text  label
0      republican committee pass bill would prohibit ...      0
1      trump treasury candidate bank accuse discrimin...      1
2      guess behind sicken ad show boy bully dad vote...      0
3      michigan treasurer call quick action detroit s...      1
4      clinton urge renew fight value washington reut...      1
...                                                  ...    ...
36527  few migrant entitle join family germany study ...      1
36528  factbox countdown brexit breakthrough brussels...      1
36529  leadership german far right split hour elector...      1
36530  u suspend obama airline transparency review wa...      1
36531  u juror hear close argument iranlinked office ...      1

[36532 rows x 2 columns]

In [85]:
fake_news2=pd.read_csv("/kaggle/input/fake-newss/train.2.csv",sep=';')
fake_news2

text  label
0     trump tell million american hurricane victim r...      0
1     new york cable provider altice acc network new...      0
2     japan dentsu get small fine overtime breach de...      1
3     little kid toxic stress solve priscilla chan c...      1
4     fantasy football kicker ranking week warn some...      0
...                                                 ...    ...
3335  movie studio join disneyled service link digit...      1
3336  gordon strachan scotland problem strachan scot...      1
3337  athenia wreck first british ship torpedo ww ca...      1
3338  rugby league world cup kear name uncapped trio...      1
3339  brazilian lead u million mattress plead guilty...      1

[3340 rows x 2 columns]

In [48]:
fake_news3=pd.read_csv("/kaggle/input/fake-newss/train.3.csv",sep=';')
fake_news3

text  label
0     complete sentence exploration orin langelle vo...      0
1     ten thousand people get fooled fake ballot wit...      0
2     comment sweep election first thing trump invit...      0
3     astonish chart show moderate republican endang...      1
4     clinton ekes win iowa sander kill obama admini...      1
...                                                 ...    ...
5067  cannabis protect brain traumatic injury concus...      0
5068  ooh fuck wednesday november lucas wilde ooh fu...      0
5069  hillary clinton accuse steal furniture state d...      0
5070  george w bush ethic lawyer file complaint fbi ...      0
5071  japan approve already dead tpp deal coalition ...      0

[5072 rows x 2 columns]

In [50]:
# dataf2_val=
xf2_val = tokenizer(
              text=fake_news2['text'].to_list(),
              add_special_tokens=True,
              max_length=max_length,
              truncation=True,
              padding=True,
              return_tensors='tf',
              return_token_type_ids = False,
              return_attention_mask = True,
              verbose = True)

In [52]:
yf2_val_predicted = Robsent.predict(
    x={'input_ids': xf2_val['input_ids']},
)

105/105 [==============================] - 6s 56ms/step


In [54]:
yf2_val_predicted

{'Emotion': array([[-0.8391785 , -0.24318136, -0.4249307 , ..., -0.51072335,
         -1.0737412 ,  0.24354571],
        [-0.36890268, -2.5251367 , -1.2469145 , ...,  0.15306439,
         -1.6586716 , -2.0381932 ],
        [ 3.7560728 , -1.914042  , -1.8748813 , ..., -0.40261298,
         -0.87924   , -1.9716395 ],
        ...,
        [-0.4825489 , -2.5729394 , -1.3019861 , ...,  0.06098894,
         -1.793764  , -1.8632296 ],
        [ 0.13535726, -2.5827096 , -1.4389108 , ..., -0.10734574,
         -1.7499337 , -1.9412988 ],
        [-1.5634158 , -0.60482   , -0.12746629, ..., -0.9850744 ,
         -1.2439524 , -0.60813445]], dtype=float32)}

In [79]:
import numpy as np
import tensorflow as tf
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import pandas as pd

# Assuming the previous steps to get y_val_predicted are already done

# Define the emotion labels in order based on the provided mapping
emotion_labels = ['neutral', 'love', 'happiness', 'sadness', 'relief', 'hate', 'anger', 'fun', 'enthusiasm', 'surprise', 'empty', 'worry', 'boredom']

# Extract logits for 'Emotion' in yf2_val_predicted
logits_f2 = yf2_val_predicted['Emotion']

# Apply softmax to convert logits to probabilities
probabilities_f2 = tf.nn.softmax(logits_f2, axis=-1).numpy()

# Get the index of the highest probability for each prediction
predicted_indices_f2 = np.argmax(probabilities_f2, axis=-1)

# Map the indices to the actual emotion labels
predicted_emotions_f2 = [emotion_labels[index] for index in predicted_indices_f2]

# Create a DataFrame to display the results
comparison_df_f2 = pd.DataFrame({
    'Predicted Emotion': predicted_emotions_f2
})

# Display the DataFrame
print(comparison_df_f2)


     Predicted Emotion
0             surprise
1           enthusiasm
2           enthusiasm
3           enthusiasm
4           enthusiasm
...                ...
3335        enthusiasm
3336        enthusiasm
3337        enthusiasm
3338        enthusiasm
3339          surprise

[3340 rows x 1 columns]


In [102]:
import pandas as pd
import numpy as np
import tensorflow as tf

# Load the fake_news2 dataset
# fake_news2 = pd.read_csv("/kaggle/input/fake-newss/train.2.csv", sep=';')

# Tokenize the input text
xf2_val = tokenizer(
    text=fake_news2['text'].to_list(),
    add_special_tokens=True,
    max_length=max_length,
    truncation=True,
    padding=True,
    return_tensors='tf',
    return_token_type_ids=False,
    return_attention_mask=True,
    verbose=True
)

# Predict the emotions for the tokenized text
yf2_val_predicted = Robsent.predict(
    x={'input_ids': xf2_val['input_ids']}
)

# Extract logits for 'Emotion' in yf2_val_predicted
logits_f2 = yf2_val_predicted['Emotion']

# Apply softmax to convert logits to probabilities
probabilities_f2 = tf.nn.softmax(logits_f2, axis=-1).numpy()

# Get the index of the highest probability for each prediction
predicted_indices_f2 = np.argmax(probabilities_f2, axis=-1)

# Define the emotion labels in order based on the provided mapping
emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

# Map the indices to the actual emotion labels
predicted_emotions_f2 = [emotion_labels[index] for index in predicted_indices_f2]

# Add the predicted emotions as a new column to the fake_news2 DataFrame
fake_news2['Predicted Emotion'] = predicted_emotions_f2

# Display the DataFrame with the new column
fake_news2

fake_news2.to_csv("/kaggle/working/fake_news2_with_prediction.csv", index=False)

fake_news2['Predicted Emotion'].value_counts()

105/105 [==============================] - 6s 57ms/step


Predicted Emotion
neutral       2885
relief         117
surprise       109
fun             41
anger           41
love            38
happiness       30
worry           28
empty           27
hate            16
sadness          6
enthusiasm       2
Name: count, dtype: int64

In [95]:
fake_news2.to_csv("/kaggle/working/fake_news2_with_prediction.csv", index=False)

In [100]:
fake_news2['Predicted Emotion'].value_counts()

Predicted Emotion
neutral       2885
relief         117
surprise       109
fun             41
anger           41
love            38
happiness       30
worry           28
empty           27
hate            16
sadness          6
enthusiasm       2
Name: count, dtype: int64

In [111]:
import pandas as pd
import numpy as np
import tensorflow as tf

# Load the fake_news2 dataset
# fake_news2 = pd.read_csv("/kaggle/input/fake-newss/train.2.csv", sep=';')

with strategy.scope():

# Tokenize the input text
    xf_val = tokenizer(
        text=fake_news['text'].to_list(),
        add_special_tokens=True,
        max_length=max_length,
        truncation=True,
        padding=True,
        return_tensors='tf',
        return_token_type_ids=False,
        return_attention_mask=True,
        verbose=True
    )

    # Predict the emotions for the tokenized text
    yf_val_predicted = Robsent.predict(
        x={'input_ids': xf_val['input_ids']}
    )

    # Extract logits for 'Emotion' in yf2_val_predicted
    logits_f = yf_val_predicted['Emotion']

    # Apply softmax to convert logits to probabilities
    probabilities_f = tf.nn.softmax(logits_f, axis=-1).numpy()

    # Get the index of the highest probability for each prediction
    predicted_indices_f = np.argmax(probabilities_f, axis=-1)

    # Define the emotion labels in order based on the provided mapping
    emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

    # Map the indices to the actual emotion labels
    predicted_emotions_f = [emotion_labels[index] for index in predicted_indices_f]

    # Add the predicted emotions as a new column to the fake_news2 DataFrame
    fake_news['Predicted Emotion'] = predicted_emotions_f

# Display the DataFrame with the new column
    fake_news

    fake_news.to_csv("/kaggle/working/fake_news_with_prediction.csv", index=False)

    fake_news['Predicted Emotion'].value_counts()

521/521 [==============================] - 29s 56ms/step


In [112]:
fake_news['Predicted Emotion'].value_counts()

Predicted Emotion
neutral       14028
relief          742
surprise        294
fun             277
anger           260
worry           236
love            223
empty           185
happiness       164
hate            145
sadness          64
enthusiasm       28
Name: count, dtype: int64

In [109]:
import pandas as pd
import numpy as np
import tensorflow as tf

# Load the fake_news2 dataset
# fake_news2 = pd.read_csv("/kaggle/input/fake-newss/train.2.csv", sep=';')

with strategy.scope():
    # Tokenize the input text
    xf1_val = tokenizer(
        text=fake_news1['text'].to_list(),
        add_special_tokens=True,
        max_length=max_length,
        truncation=True,
        padding=True,
        return_tensors='tf',
        return_token_type_ids=False,
        return_attention_mask=True,
        verbose=True
    )

    # Predict the emotions for the tokenized text
    yf1_val_predicted = Robsent.predict(
        x={'input_ids': xf1_val['input_ids']}
    )

    # Extract logits for 'Emotion' in yf2_val_predicted
    logits_f1 = yf1_val_predicted['Emotion']

    # Apply softmax to convert logits to probabilities
    probabilities_f1 = tf.nn.softmax(logits_f1, axis=-1).numpy()

    # Get the index of the highest probability for each prediction
    predicted_indices_f1 = np.argmax(probabilities_f1, axis=-1)

    # Define the emotion labels in order based on the provided mapping
    emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

    # Map the indices to the actual emotion labels
    predicted_emotions_f1 = [emotion_labels[index] for index in predicted_indices_f1]

    # Add the predicted emotions as a new column to the fake_news2 DataFrame
    fake_news1['Predicted Emotion'] = predicted_emotions_f1

    # Display the DataFrame with the new column
    fake_news1

    fake_news1.to_csv("/kaggle/working/fake_news1_with_prediction.csv", index=False)

    fake_news1['Predicted Emotion'].value_counts()

1142/1142 [==============================] - 63s 55ms/step


In [113]:
    fake_news1['Predicted Emotion'].value_counts()

Predicted Emotion
neutral       30342
relief         1484
fun             943
anger           673
worry           657
surprise        622
hate            595
love            423
empty           351
happiness       265
sadness         137
enthusiasm       40
Name: count, dtype: int64

In [110]:
import pandas as pd
import numpy as np
import tensorflow as tf

# Load the fake_news2 dataset
# fake_news2 = pd.read_csv("/kaggle/input/fake-newss/train.2.csv", sep=';')

with strategy.scope():
# Tokenize the input text
    xf3_val = tokenizer(
        text=fake_news3['text'].to_list(),
        add_special_tokens=True,
        max_length=max_length,
        truncation=True,
        padding=True,
        return_tensors='tf',
        return_token_type_ids=False,
        return_attention_mask=True,
        verbose=True
    )

    # Predict the emotions for the tokenized text
    yf3_val_predicted = Robsent.predict(
        x={'input_ids': xf3_val['input_ids']}
    )

    # Extract logits for 'Emotion' in yf2_val_predicted
    logits_f3 = yf3_val_predicted['Emotion']

    # Apply softmax to convert logits to probabilities
    probabilities_f3 = tf.nn.softmax(logits_f3, axis=-1).numpy()

    # Get the index of the highest probability for each prediction
    predicted_indices_f3 = np.argmax(probabilities_f3, axis=-1)

    # Define the emotion labels in order based on the provided mapping
    emotion_labels = ['anger', 'boredom', 'empty', 'enthusiasm', 'fun', 'happiness', 'hate', 'love', 'neutral', 'relief', 'sadness', 'surprise', 'worry']

    # Map the indices to the actual emotion labels
    predicted_emotions_f3 = [emotion_labels[index] for index in predicted_indices_f3]

    # Add the predicted emotions as a new column to the fake_news2 DataFrame
    fake_news3['Predicted Emotion'] = predicted_emotions_f3

    # Display the DataFrame with the new column
    fake_news3

    fake_news3.to_csv("/kaggle/working/fake_news3_with_prediction.csv", index=False)

    fake_news3['Predicted Emotion'].value_counts()

159/159 [==============================] - 9s 54ms/step


In [114]:
    fake_news3['Predicted Emotion'].value_counts()

Predicted Emotion
neutral       4282
relief         230
surprise        94
worry           93
anger           82
fun             71
empty           59
love            53
hate            39
happiness       33
sadness         26
enthusiasm      10
Name: count, dtype: int64

In [115]:
fake_news3['label'].value_counts()

label
0    2536
1    2536
Name: count, dtype: int64